In [ ]:
!unzip /content/mininet-idsL-main.zip

Archive:  /content/mininet-idsL-main.zip
05e2cf8fda7f1d0d4d5814604663b419c2fc7dad
   creating: mininet-idsL-main/
  inflating: mininet-idsL-main/attack_os_port_scan.csv  
  inflating: mininet-idsL-main/blocker.py  
  inflating: mininet-idsL-main/data_collector.py  
  inflating: mininet-idsL-main/data_collector_attack.py  
  inflating: mininet-idsL-main/external_mininet.py  
  inflating: mininet-idsL-main/l4_switch.py  
  inflating: mininet-idsL-main/l4_switch_moniter.py  
  inflating: mininet-idsL-main/normal_iperf.csv  
  inflating: mininet-idsL-main/normal_iperf.py  
  inflating: mininet-idsL-main/ofctl_rest.py  
  inflating: mininet-idsL-main/ryu_moniter.py  


# **Reading dataset**

In [ ]:
import pandas as pd

In [ ]:
columns = [

          'src',
          'dst',
          'table_id',
          'ip_bytes',
          'ip_packet',
          'ip_duration',
          'in_port',
          'dl_dst',
          'port_bytes',
          'port_packet',
          'port_flow_count',
          'table_active_count',
          'table_lookup_count',
          'table_matched_count',
          'port_rx_packets',
          'port_tx_packets',
          'port_rx_bytes',
          'port_tx_bytes',
          'port_rx_dropped',
          'port_tx_dropped',
          'port_rx_errors',
          'port_tx_errors',
          'port_rx_frame_err',
          'port_rx_over_err',
          'port_rx_crc_err',
          'port_collisions',
          'port_duration_sec'

]




In [ ]:
df_normal = pd.read_csv("/content/mininet-idsL-main/normal_iperf.csv",
                        header=None)

In [ ]:
df_normal.columns = columns

In [ ]:
df_normal['label'] = 0

In [ ]:
df_attack = pd.read_csv("/content/mininet-idsL-main/attack_os_port_scan.csv",
                        header=None)

In [ ]:
df_attack.columns = columns

In [ ]:
df_attack['label'] = 1

# **Merging datasets**

In [ ]:
df = pd.concat([df_normal, df_attack])

# **EDA**

In [ ]:
df['label'].value_counts()

1    38247
0    36076
Name: label, dtype: int64

In [ ]:
df.columns

Index(['src', 'dst', 'table_id', 'ip_bytes', 'ip_packet', 'ip_duration',
       'in_port', 'dl_dst', 'port_bytes', 'port_packet', 'port_flow_count',
       'table_active_count', 'table_lookup_count', 'table_matched_count',
       'port_rx_packets', 'port_tx_packets', 'port_rx_bytes', 'port_tx_bytes',
       'port_rx_dropped', 'port_tx_dropped', 'port_rx_errors',
       'port_tx_errors', 'port_rx_frame_err', 'port_rx_over_err',
       'port_rx_crc_err', 'port_collisions', 'port_duration_sec', 'label'],
      dtype='object')

In [ ]:
# remove duration = 0
df = df[~(df['ip_duration'] == 0)]

In [ ]:
df = df[~((df['port_packet'] == 0) | (df['ip_packet'] == 0))]

In [ ]:
# identity features
identity_features = [
    'src', 'dst', 'table_id', 'in_port', 'dl_dst'
]

In [ ]:
df = df.drop(columns=identity_features)

In [ ]:
df

ip_bytes  ip_packet  ip_duration  port_bytes  port_packet  \
2        396144        262            1      396144          262   
4        662256        438            2      662256          438   
5        925344        612            3      925344          612   
6       1189944        787            4     1189944          787   
7       1453032        961            5     1453032          961   
...         ...        ...          ...         ...          ...   
38238       150          2            1       28737          207   
38239        66          1            1       27983          196   
38242       348          5            1       35330          163   
38243      4626          2            1       35452          165   
38246       120          2            2        7214          106   

       port_flow_count  table_active_count  table_lookup_count  \
2                    1                   3             1332991   
4                    1                   2             1333167   
5                    1                   2             1333341   
6                    1                   2             1333516   
7                    1                   2             1333692   
...                ...                 ...                 ...   
38238               68                  81             8728149   
38239               64                  77             8728151   
38242               48                  58             8728595   
38243               48                  58             8728596   
38246              204                 298             8734007   

       table_matched_count  port_rx_packets  ...  port_rx_dropped  \
2                  1332988           375886  ...                0   
4                  1333164           376070  ...                0   
5                  1333338           376236  ...                0   
6                  1333513           376423  ...                0   
7                  1333689           376580  ...                0   
...                    ...              ...  ...              ...   
38238              8726766          7769692  ...                0   
38239              8726768          7769693  ...                0   
38242              8727212          7770099  ...                0   
38243              8727213          7770100  ...                0   
38246              8732624          7774299  ...                0   

       port_tx_dropped  port_rx_errors  port_tx_errors  port_rx_frame_err  \
2                    0               0               0                  0   
4                    0               0               0                  0   
5                    0               0               0                  0   
6                    0               0               0                  0   
7                    0               0               0                  0   
...                ...             ...             ...                ...   
38238                0               0               0                  0   
38239                0               0               0                  0   
38242                0               0               0                  0   
38243                0               0               0                  0   
38246                0               0               0                  0   

       port_rx_over_err  port_rx_crc_err  port_collisions  port_duration_sec  \
2                     0                0                0                 56   
4                     0                0                0                 57   
5                     0                0                0                 58   
6                     0                0                0                 59   
7                     0                0                0                 60   
...                 ...              ...              ...                ...   
38238                 0                0                0              49172   
382

In [ ]:
df.describe()

ip_bytes      ip_packet   ip_duration    port_bytes    port_packet  \
count  4.837900e+04   48379.000000  48379.000000  4.837900e+04   48379.000000   
mean   2.155583e+09   77077.738957      4.659873  2.164911e+09   77464.882222   
std    5.866181e+09  137771.953266      3.918071  5.884056e+09  138093.058716   
min    6.000000e+01       1.000000      1.000000  6.000000e+01       1.000000   
25%    1.980000e+02       2.000000      2.000000  1.749650e+04     123.500000   
50%    5.927040e+05     392.000000      3.000000  6.592320e+05     479.000000   
75%    1.231847e+07  113653.000000      7.000000  1.243093e+07  114989.000000   
max    3.878637e+10  757671.000000     17.000000  3.878637e+10  757671.000000   

       port_flow_count  table_active_count  table_lookup_count  \
count     48379.000000        48379.000000        4.837900e+04   
mean         37.520432           47.343517        2.839990e+08   
std          76.083719          102.987091        3.084351e+08   
min           1.000000            1.000000        2.902420e+05   
25%           1.000000            3.000000        5.397922e+06   
50%           1.000000            3.000000        1.514868e+08   
75%          53.000000           61.000000        5.786826e+08   
max         857.000000         1188.000000        8.947331e+08   

       table_matched_count  port_rx_packets  ...  port_rx_dropped  \
count         4.837900e+04     4.837900e+04  ...          48379.0   
mean          2.839985e+08     5.670287e+07  ...              0.0   
std           3.084356e+08     5.928853e+07  ...              0.0   
min           2.888590e+05     6.686900e+04  ...              0.0   
25%           5.396538e+06     4.873375e+06  ...              0.0   
50%           1.514868e+08     2.783889e+07  ...              0.0   
75%           5.786826e+08     1.120011e+08  ...              0.0   
max           8.947331e+08     1.824645e+08  ...              0.0   

       port_tx_dropped  port_rx_errors  port_tx_errors  port_rx_frame_err  \
count          48379.0         48379.0         48379.0            48379.0   
mean               0.0             0.0             0.0                0.0   
std                0.0             0.0             0.0                0.0   
min                0.0             0.0             0.0                0.0   
25%                0.0             0.0             0.0                0.0   
50%                0.0             0.0             0.0                0.0   
75%                0.0             0.0             0.0                0.0   
max                0.0             0.0             0.0                0.0   

       port_rx_over_err  port_rx_crc_err  port_collisions  port_duration_sec  \
count           48379.0          48379.0          48379.0       48379.000000   
mean                0.0              0.0              0.0       25502.180512   
std                 0.0              0.0              0.0       13963.208241   
min                 0.0              0.0              0.0          56.000000   
25%                 0.0              0.0              0.0       13746.000000   
50%                 0.0              0.0              0.0       24907.000000   
75%                 0.0              0.0              0.0       37359.500000   
max                 0.0              0.0              0.0       51389.000000   

              label  
count  48379.000000  
mean       0.408462  
std        0.491555  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        1.000000  
max        1.000000  

[8 rows x 23 columns]

In [ ]:
df.columns

Index(['ip_bytes', 'ip_packet', 'ip_duration', 'port_bytes', 'port_packet',
       'port_flow_count', 'table_active_count', 'table_lookup_count',
       'table_matched_count', 'port_rx_packets', 'port_tx_packets',
       'port_rx_bytes', 'port_tx_bytes', 'port_rx_dropped', 'port_tx_dropped',
       'port_rx_errors', 'port_tx_errors', 'port_rx_frame_err',
       'port_rx_over_err', 'port_rx_crc_err', 'port_collisions',
       'port_duration_sec', 'label'],
      dtype='object')

In [ ]:
# remove features with varience zero
zero_var_features = ['port_rx_dropped', 'port_tx_dropped',
       'port_rx_errors', 'port_tx_errors', 'port_rx_frame_err',
       'port_rx_over_err', 'port_rx_crc_err', 'port_collisions']

df = df.drop(columns=zero_var_features)

In [ ]:
df['ip_bytes_sec'] = df['ip_bytes'] / df['ip_duration']
df['ip_packets_sec'] = df['ip_packet'] / df['ip_duration']
df['ip_bytes_packet'] = df['ip_bytes'] / df['ip_packet']
df['port_bytes_sec'] = df['port_bytes'] / df['ip_duration']
df['port_packet_sec'] = df['port_packet'] / df['ip_duration']
df['port_flow_count_sec'] = df['port_flow_count'] / df['ip_duration']
df['table_matched_lookup'] = df['table_matched_count'] / df['table_lookup_count']
df['port_rx_packets_sec'] = df['port_rx_packets'] / df['port_duration_sec']
df['port_tx_packets_sec'] = df['port_tx_packets'] / df['port_duration_sec']
df['port_rx_bytes_sec'] = df['port_rx_bytes'] / df['port_duration_sec']
df['port_tx_bytes_sec'] = df['port_tx_bytes'] / df['port_duration_sec']


In [ ]:
native_features = [
    'ip_bytes', 'ip_packet', 'ip_duration',
    'port_bytes', 'ip_packet', 'port_bytes',
    'port_packet', 'port_flow_count', 'table_matched_count',
    'table_lookup_count', 'port_rx_packets', 'port_duration_sec',
    'port_tx_packets', 'port_rx_bytes', 'port_tx_bytes'
]

df = df.drop(columns=native_features)

In [ ]:
df

table_active_count  label  ip_bytes_sec  ip_packets_sec  \
2                       3      0      396144.0          262.00   
4                       2      0      331128.0          219.00   
5                       2      0      308448.0          204.00   
6                       2      0      297486.0          196.75   
7                       2      0      290606.4          192.20   
...                   ...    ...           ...             ...   
38238                  81      1         150.0            2.00   
38239                  77      1          66.0            1.00   
38242                  58      1         348.0            5.00   
38243                  58      1        4626.0            2.00   
38246                 298      1          60.0            1.00   

       ip_bytes_packet  port_bytes_sec  port_packet_sec  port_flow_count_sec  \
2               1512.0        396144.0           262.00             1.000000   
4               1512.0        331128.0           219.00             0.500000   
5               1512.0        308448.0           204.00             0.333333   
6               1512.0        297486.0           196.75             0.250000   
7               1512.0        290606.4           192.20             0.200000   
...                ...             ...              ...                  ...   
38238             75.0         28737.0           207.00            68.000000   
38239             66.0         27983.0           196.00            64.000000   
38242             69.6         35330.0           163.00            48.000000   
38243           2313.0         35452.0           165.00            48.000000   
38246             60.0          3607.0            53.00           102.000000   

       table_matched_lookup  port_rx_packets_sec  port_tx_packets_sec  \
2                  0.999998          6712.250000          3039.267857   
4                  0.999998          6597.719298          2985.947368   
5                  0.999998          6486.827586          2934.465517   
6                  0.999998          6380.050847          2884.728814   
7                  0.999998          6276.333333          2836.666667   
...                     ...                  ...                  ...   
38238              0.999842           158.010494            32.147218   
38239              0.999842           158.010514            32.147218   
38242              0.999842           157.986641            32.141800   
38243              0.999842           157.986662            32.141800   
38246              0.999842           158.010996            32.154021   

       port_rx_bytes_sec  port_tx_bytes_sec  
2           3.549138e+08      200709.142857  
4           3.486921e+08      197187.929825  
5           3.426845e+08      193788.137931  
6           3.368811e+08      190503.593220  
7           3.312703e+08      187329.233333  
...                  ...                ...  
38238       2.634891e+04        2479.552937  
38239       2.634891e+04        2479.552937  
38242       2.634495e+04        2479.765931  
38243       2.634496e+04        2479.765931  
38246       2.634041e+04        2480.299262  

[48379 rows x 13 columns]

In [ ]:
df['label'].value_counts()

0    28618
1    19761
Name: label, dtype: int64

In [ ]:
df.to_excel('data.xlsx', index=False)

# **Train validation test split**

In [ ]:
from sklearn.model_selection import train_test_split
import numpy as np

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(df.drop(columns='label'), df['label'],
                                                    test_size=0.1,
                                                    stratify=df['label'],
                                                    random_state=42)

In [ ]:
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train,
                                                    test_size=0.1,
                                                    stratify=y_train,
                                                    random_state=42)

# **Scaling features**

In [ ]:
from sklearn.preprocessing import RobustScaler

In [ ]:
scalar = RobustScaler()
X_train = scalar.fit_transform(X_train)
X_test = scalar.transform(X_test)
X_val = scalar.transform(X_val)

In [ ]:
y_train = np.asarray(y_train)
y_validation = np.asarray(y_val)
y_test = np.asarray(y_test)

In [ ]:
X_train.shape

(39186, 12)

In [ ]:
y_train.shape

(39186,)

# **Model evaluation metrics**

In [ ]:
from sklearn.metrics import classification_report

def compute_classification_report(y_true, y_pred):
  target_names = ['Normal', 'attack']
  print(classification_report(y_true, y_pred, target_names=target_names, digits=4))


# **Nearest Neighbors Classification**

In [ ]:
from sklearn.neighbors import KNeighborsClassifier
import time


In [ ]:
model = KNeighborsClassifier(n_neighbors=1)

In [ ]:
start = time.time()
model.fit(X_train, y_train)
end = time.time()
print(end - start)

0.08103489875793457


In [ ]:
y_pred_train = model.predict(X_train)

In [ ]:
y_pred_validation = model.predict(X_val)

In [ ]:
start = time.time()
y_pred_test =  model.predict(X_test)
end = time.time()
print(end - start)
print(X_test.shape)
th = X_test.shape[0] / (end - start)
print(th)

0.16826367378234863
(4838, 12)
28752.492390354077


In [ ]:
compute_classification_report(y_train, y_pred_train)

              precision    recall  f1-score   support

      Normal     1.0000    1.0000    1.0000     23180
      attack     1.0000    1.0000    1.0000     16006

    accuracy                         1.0000     39186
   macro avg     1.0000    1.0000    1.0000     39186
weighted avg     1.0000    1.0000    1.0000     39186



In [ ]:
compute_classification_report(y_validation, y_pred_validation)

              precision    recall  f1-score   support

      Normal     1.0000    1.0000    1.0000      2576
      attack     1.0000    1.0000    1.0000      1779

    accuracy                         1.0000      4355
   macro avg     1.0000    1.0000    1.0000      4355
weighted avg     1.0000    1.0000    1.0000      4355



In [ ]:
compute_classification_report(y_test, y_pred_test)

              precision    recall  f1-score   support

      Normal     1.0000    1.0000    1.0000      2862
      attack     1.0000    1.0000    1.0000      1976

    accuracy                         1.0000      4838
   macro avg     1.0000    1.0000    1.0000      4838
weighted avg     1.0000    1.0000    1.0000      4838



# **PCA**

In [ ]:
from sklearn.decomposition import PCA

In [ ]:
pca = PCA(n_components=3)

In [ ]:
X_train_pca = pca.fit_transform(X_train)

In [ ]:
X_val_pca = pca.transform(X_val)

In [ ]:
X_test_pca = pca.transform(X_test)

In [ ]:
(1 - sum(pca.explained_variance_ratio_)) * 100

0.0025852505195933517

In [ ]:
model = KNeighborsClassifier(n_neighbors=1)

In [ ]:
start = time.time()
model.fit(X_train_pca, y_train)
end = time.time()
print(end - start)

0.031194686889648438


In [ ]:
y_pred_train = model.predict(X_train_pca)

In [ ]:
y_pred_validation = model.predict(X_val_pca)

In [ ]:
start = time.time()
y_pred_test =  model.predict(X_test_pca)
end = time.time()
print(end - start)
print(X_test_pca.shape)
th = X_test_pca.shape[0] / (end - start)
print(th)

0.12552285194396973
(4838, 3)
38542.78264932638


In [ ]:
compute_classification_report(y_train, y_pred_train)

              precision    recall  f1-score   support

      Normal     1.0000    1.0000    1.0000     23180
      attack     1.0000    1.0000    1.0000     16006

    accuracy                         1.0000     39186
   macro avg     1.0000    1.0000    1.0000     39186
weighted avg     1.0000    1.0000    1.0000     39186



In [ ]:
compute_classification_report(y_validation, y_pred_validation)

              precision    recall  f1-score   support

      Normal     1.0000    1.0000    1.0000      2576
      attack     1.0000    1.0000    1.0000      1779

    accuracy                         1.0000      4355
   macro avg     1.0000    1.0000    1.0000      4355
weighted avg     1.0000    1.0000    1.0000      4355



In [ ]:
compute_classification_report(y_test, y_pred_test)

              precision    recall  f1-score   support

      Normal     0.9997    1.0000    0.9998      2862
      attack     1.0000    0.9995    0.9997      1976

    accuracy                         0.9998      4838
   macro avg     0.9998    0.9997    0.9998      4838
weighted avg     0.9998    0.9998    0.9998      4838



# **Analysis**

In [ ]:
import plotly.express as px


In [ ]:
df.columns

Index(['table_active_count', 'label', 'ip_bytes_sec', 'ip_packets_sec',
       'ip_bytes_packet', 'port_bytes_sec', 'port_packet_sec',
       'port_flow_count_sec', 'table_matched_lookup', 'port_rx_packets_sec',
       'port_tx_packets_sec', 'port_rx_bytes_sec', 'port_tx_bytes_sec'],
      dtype='object')

In [ ]:
fig = px.histogram(df, x="table_active_count", color='label')
fig.show()


In [ ]:
fig = px.histogram(df, x="ip_bytes_sec", color=df['label'])
fig.show()


In [ ]:
fig = px.histogram(df, x="ip_packets_sec", color='label')
fig.show()


In [ ]:
fig = px.histogram(df, x="ip_bytes_packet", color='label')
fig.show()


In [ ]:
fig = px.histogram(df, x="port_flow_count_sec", color='label')
fig.show()

In [ ]:
fig = px.histogram(df, x="table_matched_lookup", color='label')
fig.show()

In [ ]:
fig = px.histogram(df, x="port_tx_packets_sec", color='label')
fig.show()

In [ ]:
fig = px.histogram(df, x="port_rx_bytes_sec", color='label')
fig.show()

In [ ]:
fig = px.histogram(df, x="port_tx_bytes_sec", color='label')
fig.show()